# Практическое задание 2 (часть 1)

# Определение частей речи с помощью скрытой марковской модели

## курс "Математические методы анализа текстов"


### ФИО: Власов Андрей Валерьевич

## Введение

### Постановка задачи

В данной лабораторной работе вам предстоит обучить скрытую марковскую модель на размеченных данных и реализовать алгоритм Витерби для задачи POS-теггинга (определение частей речи слов в тексте), а также ознакомиться с использованием  ряда POS-теггеров из библиотеки NLTK.

### Комментарии и советы

1. Для выполнения потребуются модули Python numpy, nltk.

2. Все необходимые для выполнения задания данные либо приложены, либо могут быть скачаны с помощью nltk.download().

3. Посмотреть параметры конструктора и других методов классов можно набрав и выполнив в ячейке с кодом '?full_method_name'.

### Задача определения частей речи (POS)

Мы будем решать задачу определения частей речи (POS-теггинга) с помощью скрытой марковской модели (HMM). Формула совместной плотности наблюдаемых и скрытых переменных задается как

$$ p(x, t) = p(t) p(x|t) = p(t_1)  \prod_{i=2}^{N_x} p(t_i|t_{i-1}) \prod_{i=1}^{N_x} p(x_i|t_i)$$

#### Переменные модели

- наблюдаемые переменные $X$ - словарь корпуса;

- скрытые переменные $T$ - множество POS-тегов.

- x - одно предложение, $N_x$ - длина предложения

- t - теги одного предложения, $N_t$ - длина вектора меток

#### Параметры модели

- матрица вероятностей переходов $A \in \mathbb{R}^{|T| \times |T|}$, $A_{ij} = p(t_s=i|t_{s-1}=j) \; \forall s$

- матрица выходных вероятностей $B \in \mathbb{R}^{|X| \times |T|}$, $B_{ij} = p(x_s =i|t_s =j) \; \forall s$

- вектор начальных вероятностей $C \in \mathbb{R}^{|T|}$, $C_i = p(t_1=i)$


#### Обучение модели

* Для обучения параметров $A$ и $B$ используется метод максимума правдоподобия. Оценки вычисляются на основе частот совстречаемости тегов и тегов со словами ():

$$a_{ij} = \frac{\sum_{t}\sum_{s=2}^{N_t} \mathbb{I}[t_{s} = i, t_{s - 1} = j]}{\sum_{t}\sum_{s=2}^{N_t} \mathbb{I}[t_{s} = j]}$$

$$b_{ij} = \frac{\sum_{t, x}\sum_{s=1}^{N_t} \mathbb{I}[x_{s} = i, t_{s} = j]}{\sum_{t, x}\sum_{s=1}^{N_t} \mathbb{I}[t_{s} = j]}$$

* Параметры $C$ можно аналогично вычислять по частотам или считать распределение $p(t_1)$ равномерным

#### Применение модели

Применение модели на новых данных реализуется с помощью алгоритма Витерби.Это алгоритм динамиеского программирования, с помощью которого мы будем находить наиболее вероятную последовательность скрытых состояний модели для фиксированной последовательности слов:

$$ \hat{t} = \arg \max_{t} p(t|x) = \arg \max_{t} p(x, t) $$

Определим функцию, определяющую максимальную вероятность последовательности, заканчивающейся на $i$-ой позиции в состоянии $k$:

$$\delta(k, i) = \max_{t_1, \dots t_{i-1}} p(x_1, \dots x_i, t_1, \dots t_i=k)$$

Тогда $\max_{k} \delta(k, N_x)$ - максимальная вероятность всей последовательности. А состояния, на которых эта вероятность достигается - ответ задачи.

Алгоритм Витерби заключается в последовательном пересчете функции $\delta(k, i)$ по формуле:

$$\delta(k, i) = \max_{m} \delta(m, i-1) p(t_i = k|t_{i-1} = m) p(x_i|t_i=k) $$

Аналогично пересчитывается функция, определяющая, на каком состоянии этот максимум достигается:

$$s(k, i) = \arg \max_{m} \delta(m, i-1) p(t_i = k|t_{i-1} = m) p(x_i|t_i=k) $$


На практике это означает заполнение двумерных массивов размерности: (длина последовательности) $\times$ (количество возможных состояний). Когда массивы заполнены, $\arg \max_{k} \delta(k, N_x)$ говорит о последнем состоянии. Начиная с него можно восстановить все состояния по массиву $s$. 

Осталось уточнить, как стартовать последовательный пересчет (чем заполнить первый столбец массива вероятностей):

$$\delta(k, 1) = p(k) p(x_1|t_1=k)$$

Подробнее о HMM можно прочитать по [ссылке](https://web.stanford.edu/~jurafsky/slp3/A.pdf)

## Часть 1. Загрузка корпуса (1 балл)

Загрузите brown корпус с универсальной системой тегирования. Для этого вам понадобятся ресурсы brown и universal_tagset из nltk.download().  

Так как каждый конкретный датасет может использовать свою систему тегов, в NLTK предусмотрено универсальное множество тегов и возможность приведения к нему других систем. Это множество включает в себя следующие теги:


- ADJ - adjective (new, good, high, ...)
- ADP - adposition	(on, of, at, ...)
- ADV - adverb	(really, already, still, ...)
- CONJ	- conjunction	(and, or, but, ...)
- DET - determiner, article	(the, a, some, ...)
- NOUN	- noun	(year, home, costs, ...)
- NUM - numeral	(twenty-four, fourth, 1991, ...)
- PRT -	particle (at, on, out, ...)
- PRON - pronoun (he, their, her, ...)
- VERB - verb (is, say, told, ...)
- .	- punctuation marks	(. , ;)
- X	- other	(ersatz, esprit, dunno, ...)

Обратите внимание, что тегсеты в корпусах текстов и в различных теггерах могут быть разными. Проверять это можно, глядя на сами теги, а симптом - подозрительно низкое качество теггирования. В таких случаях рекомендуется всё приводить сперва к универсальному тегсету, а потом уже мерять качество. Полезной может оказаться эта ссылка http://www.nltk.org/_modules/nltk/tag/mapping.html

In [9]:
import nltk
nltk.download('brown')
nltk.download('universal_tagset')

from nltk.corpus import brown

from sklearn.model_selection import train_test_split

from collections import OrderedDict, deque
import pandas as pd
import numpy as np

brown_tagged_sents = brown.tagged_sents(tagset="universal")

# you code here

[nltk_data] Downloading package brown to /home/andrey/nltk_data...
[nltk_data]   Package brown is already up-to-date!
[nltk_data] Downloading package universal_tagset to
[nltk_data]     /home/andrey/nltk_data...
[nltk_data]   Package universal_tagset is already up-to-date!


Проанализируйте данные, с которыми Вы работаете. В частности, ответьте на вопросы:
- Каков общий объем датасета, формат?
- Приведены ли слова к нижнему регистру? Чем  это нам может в дальнейшем помешать?
- Как распределены слова в корпусе?  Как распределены теги в корпусе? Подсчитайте частоты и отобразите любым удобным для Вас способом. Проинтерпретируйте полученные результаты.

In [10]:
from tqdm import tqdm_notebook

In [11]:
cnt_word = 0
words = []
tags = []

tags = [tag for sents in brown_tagged_sents for (word, tag) in sents] # наши теги
words = [word for sents in brown_tagged_sents for (word, tag) in sents] # наши слова

tag_num = pd.Series(tags).value_counts(ascending=False) # тег - кол-во тега с корпусе
word_num = pd.Series(words).value_counts(ascending=False) # слово - кол-во слова с корпусе
        
print('Объем датасета #sentences =',len(brown_tagged_sents),'#word =',len(word_num),'\nформат =',type(brown_tagged_sents))

Объем датасета #sentences = 57340 #word = 56057 
формат = <class 'nltk.corpus.reader.util.ConcatenatedCorpusView'>


In [13]:
fdist_word = nltk.FreqDist(words)
fdist_word

FreqDist({'the': 62713, ',': 58334, '.': 49346, 'of': 36080, 'and': 27915, 'to': 25732, 'a': 21881, 'in': 19536, 'that': 10237, 'is': 10011, ...})

In [14]:
fdist_tag = nltk.FreqDist(tags)
fdist_tag

FreqDist({'NOUN': 275558, 'VERB': 182750, '.': 147565, 'ADP': 144766, 'DET': 137019, 'ADJ': 83721, 'ADV': 56239, 'PRON': 49334, 'CONJ': 38151, 'PRT': 29829, ...})

Cделайте случайное разбиение выборки на обучение и контроль в отношении 9:1.Если впоследствии обучение моделей будет занимать слишком много времени, работайте с подвыборкой, например, только текстами определенных категорий.

In [17]:
from sklearn.model_selection import train_test_split

In [18]:
my_brown_tagged_sents = np.array(brown.tagged_sents(tagset="universal",categories='government'))

In [19]:
X_train, X_test = train_test_split(brown_tagged_sents, train_size=0.9,random_state=1714,shuffle=True)

/home/andrey/anaconda3/lib/python3.7/site-packages/sklearn/model_selection/_split.py:2026: FutureWarning: From version 0.21, test_size will always complement train_size unless both are specified.
  FutureWarning)


In [20]:
len(X_train),len(X_test)

(51606, 5734)

## Часть 2. Скрытая марковская модель (4 балла) 

### Метод максимального правдоподобия для обучения модели

Требуется построить скрытую марковскую модель (class HiddenMarkovModel) и написать метод fit для настройки всех её параметров с помощью оценок максимального правдоподобия по размеченным данным (последовательности пар слово+тег):

- Вероятности переходов между скрытыми состояниями $p(t_i | t_{i - 1})$ посчитайте на основе частот биграмм POS-тегов.

- Вероятности эмиссий наблюдаемых состояний $p(x_i | t_i)$ посчитайте на основе частот "POS-тег - слово".

- Обратите внимание на проблему разреженности счетчиков и сделаейте все вероятности сглаженными по Лапласу ([add-k smoothing](https://en.wikipedia.org/wiki/Additive_smoothing)).

- Распределение вероятностей начальных состояний $p(t_1)$ задайте равномерным.


### Алгоритм Витерби для применения модели

Требуется написать метод .predict для определения частей речи на тестовой выборке. Чтобы использовать обученную модель на новых данных, необходимо реализовать алгоритм Витерби. 

В реализации рекомендуется перейти к логарифмам, т.к. произведение большого числа маленьких вероятностей может приводить к вычислительным ошибкам.

In [24]:
from collections import OrderedDict, deque
import pandas as pd
import numpy as np

In [25]:
class HiddenMarkovModel:    
    def __init__(self, k_smoothing=1.0,lower=False):
        """
        k_smoothing : float, constant in add-k-smoothing
        """
        self.k_smoothing = k_smoothing
        self.lower = lower
        
    def fit(self, train_tokens_tags_list):
        """
        Fit the model using maximum likelihood method.
        
        train_tokens_tags_list: list of list of pairs (token, tag) 
        """
        tags = [tag for sent in train_tokens_tags_list
                for (word, tag) in sent]
        if self.lower:
            words = [word.lower() for sent in train_tokens_tags_list
                 for (word, tag) in sent]
        else:
            words = [word for sent in train_tokens_tags_list
                 for (word, tag) in sent]

        tag_num = pd.Series(tags).value_counts(ascending=False).sort_index()
        word_num = pd.Series(words).value_counts(ascending=False)
         
        self.tags = tag_num.index
        self.words = word_num.index
        
        A = pd.DataFrame({'{}'.format(tag) : [0] * len(tag_num) for tag in tag_num.index}, index=tag_num.index)
        B = pd.DataFrame({'{}'.format(tag) : [0] * len(word_num) for tag in tag_num.index}, index=word_num.index)
        
        # Вычисляем матрицу A и B по частотам слов и тегов
        
        # sent - предложение
        # sent[i][0] - i слово в этом предложении, sent[i][1] - i тег в этом предложении
        for sent in tqdm_notebook(train_tokens_tags_list):
            for i in range(len(sent)):
                word_0 = sent[i][0]
                if self.lower:
                    word_0 = sent[i][0].lower()
                B.loc[word_0,sent[i][1]] += 1 # текущая i-пара слово-тег (обновите матрицу B аналогично A)
                
                if len(sent) - 1 != i: # для последнего тега нет следующего тега
                    A.loc[sent[i][1], sent[i + 1][1]] += 1 # пара тег-тег
                
        
        # переходим к вероятностям
        
        # нормируем по строке, то есть по всем всевозможным следующим тегам
        A = (A+self.k_smoothing).divide(A.sum(axis=1)+len(self.tags), axis=0)
        
        # # нормируем по столбцу, то есть по всем всевозможным текущим словам
        B = (B+self.k_smoothing) / (np.sum(B, axis=0)+len(self.words))
    
        
        
        self.A = A
        self.B = B
        
        pass
    
    def predict(self, test_tokens_list):
        """
        Return predictions for test_tokens_list using viterbi algorithm.
        
        test_tokens_list : list of list of tokens
        
        return: list of list of tags
        """
        predict_tags = OrderedDict({i : np.array([]) for i in range(len(test_tokens_list))})
        self.unkonwn = []
        for i_sent in range(len(test_tokens_list)):
            
            current_sent = test_tokens_list[i_sent] # текущее предложение
            len_sent = len(current_sent) # длина предложения 
            
            q = np.zeros(shape=(len_sent + 1, len(self.tags)))
            q[0] = 1 # нулевое состояние (равномерная инициализация по всем s)
            back_point = np.zeros(shape=(len_sent + 1, len(self.tags))) # # argmax
            
            for t in range(len_sent):
                
                # если мы не встречали такое слово в обучении, то вместо него будет 
                # самое популярное слово с самым популярным тегом (вопрос 2)
                if self.lower:
                    current_sent[t] = current_sent[t].lower()
                if (current_sent[t] not in self.words):
                    self.unkonwn.append(current_sent[t])
                    current_sent[t] = self.words[0]
                    
                # через max выбираем следующий тег
                for i_s in range(len(self.tags)):
                    
                    s = self.tags[i_s]
                    
                    q[t + 1][i_s] = np.max(q[t]*
                        self.A.loc[:, s]*
                        self.B.loc[current_sent[t], s])
                    
                    
                    # argmax, чтобы восстановить последовательность тегов
                    back_point[t + 1][i_s] = (q[t] * self.A.loc[:, s]* 
                        self.B.loc[current_sent[t],s]).reset_index()[s].idxmax() # индекс 
                    
            back_point = back_point.astype('int')
            
            # выписываем теги, меняя порядок на реальный
            back_tag = deque()
            current_tag = np.argmax(q[len_sent])
            for t in range(len_sent, 0, -1):
                back_tag.appendleft(self.tags[current_tag])
                current_tag = back_point[t, current_tag]
             
            predict_tags[i_sent] = np.array(back_tag)
        return predict_tags
        pass

Обучите скрытую марковскую модель:

In [26]:
hmm = HiddenMarkovModel(k_smoothing=0)
%time hmm.fit(X_train)


CPU times: user 6min 11s, sys: 1.98 s, total: 6min 13s
Wall time: 6min 6s


In [29]:
hmm_lw = HiddenMarkovModel(k_smoothing=0,lower=True)
%time hmm_lw.fit(X_train)


CPU times: user 6min 4s, sys: 1.61 s, total: 6min 6s
Wall time: 6min


In [76]:
hmm_1 = HiddenMarkovModel(k_smoothing=1)
%time hmm_1.fit(X_train)

CPU times: user 6min 20s, sys: 2.28 s, total: 6min 22s
Wall time: 6min 14s


In [27]:
(hmm.B == 0).any(),(hmm.A == 0).any()

(.       True
 ADJ     True
 ADP     True
 ADV     True
 CONJ    True
 DET     True
 NOUN    True
 NUM     True
 PRON    True
 PRT     True
 VERB    True
 X       True
 dtype: bool, .       False
 ADJ     False
 ADP     False
 ADV     False
 CONJ    False
 DET     False
 NOUN    False
 NUM     False
 PRON    False
 PRT     False
 VERB    False
 X       False
 dtype: bool)

In [81]:
(hmm_1.B == 0).any(),(hmm_1.A == 0).any()

(.       False
 ADJ     False
 ADP     False
 ADV     False
 CONJ    False
 DET     False
 NOUN    False
 NUM     False
 PRON    False
 PRT     False
 VERB    False
 X       False
 dtype: bool, .       False
 ADJ     False
 ADP     False
 ADV     False
 CONJ    False
 DET     False
 NOUN    False
 NUM     False
 PRON    False
 PRT     False
 VERB    False
 X       False
 dtype: bool)

In [116]:
hmm_1_lw = HiddenMarkovModel(k_smoothing=1,lower=True)
# in both mtx smoothing
%time hmm_1_lw.fit(X_train)

CPU times: user 6min 8s, sys: 1.74 s, total: 6min 10s
Wall time: 6min 3s


Проверьте работу реализованного алгоритма на следующих модельных примерах, проинтерпретируйте результат.

- 'he can stay'
- 'a milk can'
- 'i saw a dog'
- 'an old saw'

In [28]:
examples = ['he can stay'.split(), 'a milk can'.split(),
            'i saw a dog'.split(), 'an old saw'.split()]
hmm.predict(examples)

OrderedDict([(0, array(['PRON', 'VERB', 'VERB'], dtype='<U4')),
             (1, array(['DET', 'NOUN', 'VERB'], dtype='<U4')),
             (2, array(['NOUN', 'VERB', 'DET', 'NOUN'], dtype='<U4')),
             (3, array(['DET', 'ADJ', 'VERB'], dtype='<U4'))])

In [35]:
hmm_lw.predict(examples)

OrderedDict([(0, array(['PRON', 'VERB', 'VERB'], dtype='<U4')),
             (1, array(['DET', 'NOUN', 'VERB'], dtype='<U4')),
             (2, array(['PRON', 'VERB', 'DET', 'NOUN'], dtype='<U4')),
             (3, array(['DET', 'ADJ', 'VERB'], dtype='<U4'))])

In [118]:
hmm_1_lw.predict(examples)

OrderedDict([(0, array(['PRON', 'VERB', 'VERB'], dtype='<U4')),
             (1, array(['DET', 'NOUN', 'VERB'], dtype='<U4')),
             (2, array(['PRON', 'VERB', 'DET', 'NOUN'], dtype='<U4')),
             (3, array(['DET', 'ADJ', 'VERB'], dtype='<U4'))])

In [77]:
hmm_1.predict(examples)

OrderedDict([(0, array(['PRON', 'VERB', 'VERB'], dtype='<U4')),
             (1, array(['DET', 'NOUN', 'VERB'], dtype='<U4')),
             (2, array(['NOUN', 'VERB', 'DET', 'NOUN'], dtype='<U4')),
             (3, array(['DET', 'ADJ', 'VERB'], dtype='<U4'))])

Примените модель к отложенной выборке Брауновского корпуса и подсчитайте точность определения тегов (accuracy). Сделайте выводы. 

In [32]:
from sklearn.metrics import accuracy_score
def score(hmm, X_test):
    k_full = 0.0
    k_right = 0.0
    for sent in tqdm_notebook(X_test):
        tags = np.array(np.array(sent)[:,1])
        words = np.array(np.array(sent)[:,0])
        predict_tags = hmm.predict([words])[0]
        k_right += np.sum(tags == predict_tags)
        k_full += len(tags)
    accuracy =  k_right / k_full
    print("Accuracy:", k_right / k_full * 100, '%')
    return accuracy

In [78]:
# all datasets
hmm_1_eval = score(hmm_1, X_test)
hmm_1_eval 

Accuracy: 92.71886332977101 %


0.9271886332977102

In [121]:
# all datasets
hmm_1_lw_eval = score(hmm_1_lw, X_test)
hmm_1_lw_eval

Accuracy: 92.98253298060582 %


0.9298253298060583

In [36]:
# all datasets
hmm_lw_eval = score(hmm_lw, X_test)
hmm_lw_eval


Accuracy: 95.13127486924641 %


0.9513127486924641

In [33]:
# all datasets
hmm_eval =score(hmm, X_test)
hmm_eval 


Accuracy: 94.99053013848587 %


0.9499053013848586

## Бонусная часть. Сравнение с готовыми POS-теггерами из NLTK (2 балла)

В прошлом пункте Вы реализовали свой POS-тегер на основе скрытой марковской модели. Теперь сравните его работу с готовыми средставми, доступными в библиотеке NLTK: http://www.nltk.org/api/nltk.tag.html

Сравните с вашей моделью любые из 4-х теггеров, представленных ниже.

При проведении экспериментов обращайте внимание на следующие моменты (и отразите их в отчете):
- Какой подход лежит в основе теггера
- На каких данных он обучен (если Вы скачали готовую модель)
- Сколько времени занимает обучение на brown корпусе (если обучаете сами)
- Какая точность получается на контролькой выборке

Сформируйте рекоммендиции о том, какую технологию Вы бы использовали, если встретитесь с задачей определения частей речи в будущем.

In [37]:
import nltk
from nltk.tag.mapping import map_tag

### 1. DefaultTagger
Простая заглушка, ставящая всем словам один и тот же pos-тег. Очевидно, для максимизации качества, мы хотим выбрать самую частотную метку из всех меток обучающей выборки, т.е. метку 'NOUN'.

In [77]:
from nltk.tag import DefaultTagger
default_tagger = DefaultTagger(u'NOUN')

default_tagger_eval = default_tagger.evaluate(gold=X_test)
default_tagger_eval

0.23855363069277685

### 2. RegexpTagger

Теггер, который присваивает слову часть речи, основываясь на регулярных выражениях. Например, ставить слову метку 'NOUN', если слово кончается на 'ness'. Ниже приведен простой пример возможных правил. В качестве backoff теггера использован DefaultTagger.



In [78]:
from nltk.tag import RegexpTagger

# Не работает
# X_test_change = [(word[0],map_tag('universal','en-ptb', word[1])) for pred in X_test for word in pred]

# regexp_tagger = RegexpTagger(regexps=[(r'^-?[0-9]+(.[0-9]+)?$', 'CD'),   # cardinal numbers
#                                       (r'(The|the|A|a|An|an)$', 'AT'),   # articles
#                                       (r'.*able$', 'JJ'),                # adjectives
#                                       (r'.*ness$', 'NN'),                # nouns formed from adjectives
#                                       (r'.*ly$', 'RB'),                  # adverbs
#                                       (r'.*s$', 'NNS'),                  # plural nouns
#                                       (r'.*ing$', 'VBG'),                # gerunds
#                                       (r'.*ed$', 'VBD'),                 # past tense verbs
#                                       (r'.*', 'NN')                      # nouns (default)
#                                      ],
#                              backoff=default_tagger)

regexp_tagger = RegexpTagger(regexps=[(r'^-?[0-9]+(.[0-9]+)?$', 'NUM'),   # cardinal numbers
                                      (r'(The|the|A|a|An|an)$', 'DET'),   # articles
                                      (r'.*able$', 'ADJ'),                # adjectives
                                      (r'.*ness$', 'ADJ'),                # nouns formed from adjectives
                                      (r'.*ly$', 'ADV'),                  # adverbs
                                      (r'.*s$', 'NOUN'),                  # plural nouns
                                      (r'.*ing$', 'VERB'),                # gerunds
                                      (r'.*ed$', 'VERB'),                 # past tense verbs
                                      (r'.*', 'NOUN')                     # nouns (default)
                                     ],
                             backoff=default_tagger)


regexp_tagger_eval = regexp_tagger.evaluate(gold=X_test)
regexp_tagger_eval

0.38454588104463866

### 3. N-грамные теггеры

В теггерах, основанных на n-граммах,  принятие решения происходит в зависимости от $n-1$ предыдущих слов и их тегов. Эти теггеры необходимо обучать по размеченной обучающей коллекции. 

Заметим, что TrigramTagger и BigramTagger работают очень плохо без указания backoff. Поэтому предлагается построить композицию, где 
в качестве backoff для UnigramTagger использовать DefaultTagger, для BigramTagger использовать UnigramTagger, для TrigramTagger  использовать BigramTagger. 

In [55]:
from nltk.tag import UnigramTagger
from nltk.tag import BigramTagger
from nltk.tag import TrigramTagger

UniTag = UnigramTagger(X_train)
BiTag = BigramTagger(X_train)
TriTag = TrigramTagger(X_train)
BiTag_with = BigramTagger(X_train, backoff=UniTag)
TriTag_with = TrigramTagger(X_train, backoff=BiTag_with)



In [44]:
UniTag.evaluate(gold=X_test)

0.9325728484300881

In [45]:
BiTag.evaluate(gold=X_test),BiTag_with.evaluate(gold=X_test)

(0.4776285381661483, 0.9409306528122883)

In [56]:
TriTag.evaluate(gold=X_test),TriTag_with.evaluate(gold=X_test)

(0.27115949331896927, 0.9406439505829612)

### 4. Stanford tagger

Скачайте предобученную модель от Стэнфорда: https://nlp.stanford.edu/software/tagger.shtml и примените к тестовым данным. 
Не забудьте преобразовать систему тэгов из 'en-ptb' в 'universal' с помощью функции map_tag.

In [47]:
from nltk.tag.stanford import StanfordPOSTagger

# Add the jar and model via their path:
stanford_dir = 'stanford-postagger-full-2018-10-16/'
jar = stanford_dir+'stanford-postagger-3.9.2.jar'
model = stanford_dir+'models/english-bidirectional-distsim.tagger'
stanford_tagger = StanfordPOSTagger(model, jar, encoding='utf8')


In [48]:
test_stanf = [[word[0] for word in sentence] for sentence in X_test]
predict = stanford_tagger.tag_sents(test_stanf)

In [49]:
predict_change = [map_tag('en-ptb', 'universal', word[1]) for pred in predict for word in pred]


In [50]:
tags_stanf = [word[1] for sentence in X_test for word in sentence ]

In [51]:
import pandas as pd
predict_change = pd.Series(predict_change)
tags_stanf_pd = pd.Series(tags_stanf)

In [76]:
StanfordPOSTagger_eval = (tags_stanf_pd == predict_change).sum() / len(tags_stanf)
StanfordPOSTagger_eval 

0.9249882712724367

### 5. Теггеры из NLTK на основе графических моделей

Обучите теггер, основанный на HMM или CRF, на основе класса из nltk.

In [53]:
from nltk.tag import HiddenMarkovModelTagger, CRFTagger

hmm_trainer = HiddenMarkovModelTagger.train(X_train)

In [75]:
HiddenMarkovModelTagger_eval = hmm_trainer.evaluate(X_test)
HiddenMarkovModelTagger_eval

0.9532327848343208

In [57]:
CRFT = CRFTagger()

In [58]:
CRFT.train(X_train,'model.crf.tagger')

In [69]:
gold_sentences =CRFT.tag_sents(test_stanf)

In [70]:
predict = [word[1] for sent in gold_sentences for word in sent]

In [71]:
predict = pd.Series(predict)

In [74]:
CRFT_eval = (tags_stanf_pd == predict).sum() / len(tags_stanf_pd)
CRFT_eval

0.9641535333877778

### Сравнение моделей

Сравните различные модели по качеству, сделайте выводы.

Посмотрим на все результаты для построенной модели без/с нижним регистром

In [86]:
print(hmm_eval,hmm_lw_eval,hmm_1_eval,hmm_1_lw_eval)

0.9499053013848586 0.9513127486924641 0.9271886332977102 0.9298253298060583


Дефолтных тэгеров

In [89]:
default_tagger_eval,regexp_tagger_eval

(0.23855363069277685, 0.38454588104463866)

N-gram моделей

In [87]:
UniTag.evaluate(gold=X_test),BiTag_with.evaluate(gold=X_test),TriTag_with.evaluate(gold=X_test)

(0.9325728484300881, 0.9409306528122883, 0.9406439505829612)

И продвинутых

In [88]:
StanfordPOSTagger_eval, HiddenMarkovModelTagger_eval,CRFT_eval

(0.9249882712724367, 0.9532327848343208, 0.9641535333877778)

Почему модель со сглаживанием работает хуже,чем без сглаживания:
 - расставляя вероятности для всех тэгов для каждого слова - не всегда хорошо, тк иногда не бывает чтобы слово использовалось в такой части речи
 - хотя с другой стороны если бы у нас была небольшая выборка, то дб работать лучше
 
Почему модель со словами без заглавных букв лучше:
 - тк меньше слов (токенов) в выборке поэтому лучше настраиваются связи и лучше оценка
 - меньше слов для оценивания, больше вероятность, что знаем это слово
 
Модель ведет себя близко к HiddenMarkovModelTagger, что надеюсь показывает, что нормально реализовал

Как видим N-gram ные модели ведут себя близко по качеству с нашей из учета слов, почему-то когда впервые обучил BiGramWithUni она была > 0.95, а TriGramWithBiGramWithUni > 0.96, что логичнее, чем ячейка выше, тк в них учитывается не только последнее слово.


